In [1]:
from bokeh.plotting import figure
from bokeh.io import show, output_notebook
from bokeh.layouts import column, row
from bokeh.models import Range1d
from bokeh.io import export_png
output_notebook()

import numpy as np

from voltagebudget import util
from voltagebudget import neurons
from voltagebudget.util import locate_firsts
from voltagebudget.util import locate_peaks
from voltagebudget.util import filter_voltages
from fakespikes import util as fsutil

from scipy.io import loadmat

from pprint import pprint

def plot_mode_example(budget_y, mode):
    times = budget_y['times']
    m = times > 0.25
                   
    # -
    p = figure(title=mode, plot_width=300, plot_height=100, toolbar_location=None)
    for n in range(N):
        v = budget_y['V_m'][n, :]
        p.line(x=times[m], y=(10e-3 * n) + v[m], color="black", alpha=0.8)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.axis.visible = False
    show(p)
    return p
    
def plot_step(budget_y):
    times = budget_y['times']
    m = times > 0.25
    
    I = budget_y['I_ext'][0, :]
    p = figure(plot_width=200, plot_height=60, tools='')
    p.line(x=times[m], y=I[m], alpha=0.5)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.axis.visible = False
    show(p)
    return p

def plot_ticks(ns, ts, t_span):
    p = figure(plot_width=200, plot_height=120, toolbar_location=None)
    p.circle(ts, ns, color="black", size=0.7)
    p.xaxis.axis_label = ''
    p.yaxis.axis_label = 'N'
    p.x_range = Range1d(*t_span)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.xaxis.major_tick_line_color = None  # turn off x-axis major ticks
    p.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks

    p.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
    p.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
    p.yaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
    p.xaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
    p.axis.visible = False
    show(p)
    
def plot_input_ticks(ns, ts):
    p = figure(plot_width=150, plot_height=80, toolbar_location=None)
    p.circle(ts, ns, color="black", size=0.7)
    p.xaxis.axis_label = ''
    p.yaxis.axis_label = ''
    p.x_range = Range1d(0, t)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.xaxis.major_tick_line_color = None  # turn off x-axis major ticks
    p.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks

    p.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
    p.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
    p.yaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
    p.xaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
    p.axis.visible = False
    show(p)

def plot_comp_example(budget_y, mode, N, t_span):                   
    times = budget_y['times']
    
    p = figure(title=mode, plot_width=200, plot_height=150, toolbar_location=None)
    for n in range(N):
        v = budget_y['V_m'][n, :]
        p.line(x=times, y=v, color="black", alpha=0.1)
    p.x_range = Range1d(*t_span)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.yaxis.axis_label = 'Membrane voltages'
    p.xaxis.axis_label = 'Time (s)'
#     p.xaxis.axis_label_text_font_size = '10pt'
    p.yaxis.axis_label_text_font_size = '10pt'
    
#     p.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks

    p.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
    p.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
    p.yaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
    p.xaxis.major_label_text_font_size = '10pt'  # turn off y-axis tick labels
    p.axis.visible = False
    show(p)
    
    return p

Loading BokehJS ...

# Neuron examples

In [2]:
modes = util.get_mode_names()
pprint(modes)

dict_keys(['heterogenous', 'regular', 'adaption', 'initial_burst', 'regular_burst', 'delayed_accelerating', 'delayed_regular_bursting', 'transient_spiking'])


In [3]:
# -
N = 1
t = 1.25

In [4]:
mode = 'regular'
params, w_in, bias_in, sigma = util.read_modes(mode)

# -
ns_y, ts_y, budget_y = neurons.adex(N, t, np.asarray([0]), np.asarray([0]), 
                                  w_in=0, bias_in=np.asarray(bias_in)*0.25, 
                                  A=0, f=0,
                                  sigma=sigma,
                                  report=None,
                                  **params)

p = plot_mode_example(budget_y, None)

WARNING    "V_l" is an internal variable of group "neurongroup", but also exists in the run namespace with the value -0.07. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "a" is an internal variable of group "neurongroup", but also exists in the run namespace with the value array([1.97490802e-09]). The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "delta_t" is an internal variable of group "neurongroup", but also exists in the run namespace with the value 0.002. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "C" is an internal variable of group "neurongroup", but also exists in the run namespace with the value 2e-10. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "tau_w" is an internal variable of group "neurongroup", but also exists in the run namespace with the value

In [5]:
mode = 'adaption'
params, w_in, bias_in, sigma = util.read_modes(mode)

# -
ns_y, ts_y, budget_y = neurons.adex(N, t, np.asarray([0]), np.asarray([0]), 
                                  w_in=0, bias_in=bias_in*0.25, 
                                  A=.25e-9, f=0,
                                  sigma=sigma,
                                  step_params=(3.5e-10, 1, 0.5),
                                  report=None,
                                  **params)

plot_mode_example(budget_y, None)

TypeError: adex() got an unexpected keyword argument 'step_params'

In [ ]:
mode = 'delayed_accelerating'
params, w_in, bias_in, sigma = util.read_modes(mode)

# -
ns_y, ts_y, budget_y = neurons.adex(N, t, np.asarray([0]), np.asarray([0]), 
                                  w_in=0, bias_in=bias_in*0.25, 
                                  A=.25e-9, f=0,
                                  sigma=sigma,
                                  step_params=(3e-10, 1, 0.5),
                                  report=None,
                                  **params)

plot_mode_example(budget_y, None)

In [ ]:
mode = 'regular_burst'
params, w_in, bias_in, sigma = util.read_modes(mode)

# -
ns_y, ts_y, budget_y = neurons.adex(N, t, np.asarray([0]), np.asarray([0]), 
                                  w_in=0, bias_in=bias_in*0.25, 
                                  A=.25e-9, f=0,
                                  sigma=sigma,
                                  step_params=(5e-10, 1, 0.5),
                                  report=None,
                                  **params)

plot_mode_example(budget_y, None)

In [ ]:
mode = 'initial_burst'
params, w_in, bias_in, sigma = util.read_modes(mode)

# -
ns_y, ts_y, budget_y = neurons.adex(N, t, np.asarray([0]), np.asarray([0]), 
                                  w_in=0, bias_in=bias_in*0.25, 
                                  A=.25e-9, f=0,
                                  sigma=sigma,
                                  step_params=(4e-10, 1, 0.5),
                                  report=None,
                                  **params)

plot_mode_example(budget_y, None)

In [ ]:
mode = 'delayed_regular_bursting'
params, w_in, bias_in, sigma = util.read_modes(mode)

# -
ns_y, ts_y, budget_y = neurons.adex(N, t, np.asarray([0]), np.asarray([0]), 
                                  w_in=0, bias_in=bias_in*0.25, 
                                  A=.25e-9, f=0,
                                  sigma=sigma,
                                  step_params=(2e-10, 1, 0.5),
                                  report=None,
                                  **params)

plot_mode_example(budget_y, None)

# Computation versus coordination

In [7]:
t = 0.4

k = 20
stim_onset = 0.1
stim_offset = 0.3
stim_rate = 12
dt = 1e-5
seed_stim = 1
ns, ts = util.poisson_impulse(
        t,
        stim_onset,
        stim_offset - stim_onset,
        stim_rate,
        n=k,
        dt=dt,
        seed=None)

plot_input_ticks(ns, ts)
print(">>> {} spikes".format(ts.size))
print(">>> {} population rate".format(ts.size / (stim_offset - stim_onset)))

>>> 49 spikes
>>> 245.00000000000003 population rate


### Regular firing

In [ ]:
#set mode
mode = 'regular'
N = 50

params, w_in, bias_in, sigma = util.read_modes(mode)
bias_in = np.asarray(bias_in)

print(w_in)

f = 30

In [ ]:
ns_y, ts_y, budget = neurons.adex(N, t, ns, ts, 
                                  w_in=w_in, 
                                  bias_in=bias_in, 
                                  sigma=0, 
                                  report=None,
                                  n_cycles=10,
                                  A=.0, f=0, **params)
plot_ticks(ns_y, ts_y, (0.05, 0.15))
plot_comp_example(budget, None, 10, (0.05, 0.15))

In [ ]:
A1 = 0.01e-9
ns_y1, ts_y1, budget1 = neurons.adex(N, t, ns, ts, 
                                  w_in=w_in, 
                                  bias_in=bias_in,
                                  E=0.01,
                                  A=A1,
                                  f=f,
                                  n_cycles=20,
                                  sigma=0, 
                                  report=None,
                                  **params)

plot_ticks(ns_y1, ts_y1, (0.05, 0.15))
plot_comp_example(budget1, None, 10, (0.05, 0.15))

In [ ]:
A2 = 0.02e-9
ns_y2, ts_y2, budget2 = neurons.adex(N, t, ns, ts, 
                                  w_in=w_in, 
                                  bias_in=bias_in,
                                  E=0.01,
                                  A=A2,
                                  f=f,
                                  n_cycles=20,
                                  sigma=0, 
                                  report=None,
                                  **params)

plot_ticks(ns_y2, ts_y2, (0.05, 0.15))
plot_comp_example(budget2, None, 10, (0.05, 0.15))

# Example oscillations

In [ ]:
from scipy.io import loadmat
import h5py

from scipy.io import loadmat
from scipy.signal import hilbert
from scipy.signal import butter, lfilter

def butter_bandpass(lowcut, highcut, fs, order=5):
    nyq = 0.5 * fs
    low = lowcut / nyq
    high = highcut / nyq
    b, a = butter(order, [low, high], btype='band')
    
    return b, a

def butter_bandpass_filter(data, lowcut, highcut, fs, order=5):
    b, a = butter_bandpass(lowcut, highcut, fs, order=order)
    y = lfilter(b, a, data)
    
    return y



In [ ]:
hippo_file = h5py.File("lfp0.mat")

In [ ]:
hippo = np.squeeze(hippo_file['lfp'].value)
hippo = butter_bandpass_filter(hippo, 1, 30, 500, order=2)
times = range(hippo.size)


In [ ]:
p = figure(plot_width=300, plot_height=100, toolbar_location=None)

p.line(x=times[:2500], y=hippo[:2500], color="black", alpha=0.8)

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
p.yaxis.axis_label = 'Membrane voltages'
p.xaxis.axis_label = 'Time (s)'
#     p.xaxis.axis_label_text_font_size = '10pt'
p.yaxis.axis_label_text_font_size = '10pt'

p.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks

p.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
p.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
p.yaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
#     p.xaxis.major_label_text_font_size = '10pt'  # turn off y-axis tick labels
p.axis.visible = False
show(p)



# Visual alpha (task)

In [ ]:
alpha = loadmat('alpha_data.mat')['oz_dat_task'][0,:]

In [ ]:
alpha = butter_bandpass_filter(alpha, 1, 30, 500, order=2)
times = range(alpha.size)

In [ ]:
p = figure(plot_width=300, plot_height=100, toolbar_location=None)

p.line(x=times[:2000], y=alpha[:2000], color="black", alpha=0.8)

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
p.yaxis.axis_label = 'Membrane voltages'
p.xaxis.axis_label = 'Time (s)'
#     p.xaxis.axis_label_text_font_size = '10pt'
p.yaxis.axis_label_text_font_size = '10pt'

p.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks

p.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
p.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
p.yaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
#     p.xaxis.major_label_text_font_size = '10pt'  # turn off y-axis tick labels
p.axis.visible = False
show(p)

# Membrane and window

In [ ]:
t = 0.4
stim_number = 40
stim_onset = 0.2
stim_offset = 0.350
stim_rate = 6
dt = 1e-5
seed_stim = 1
ns_x, ts_x = util.poisson_impulse(
        t,
        stim_onset,
        stim_offset - stim_onset,
        stim_rate,
        n=stim_number,
        dt=dt,
        seed=None)

print(">>> {} spikes".format(ts_x.size))
print(">>> {} population rate".format(ts_x.size / (stim_offset - stim_onset)))

In [ ]:
params, w_in, bias_in, sigma = util.read_modes(mode)
bias_in = np.asarray(bias_in)

N = 20
A = 0.2e-9 
ns_y, ts_y, budget_y = neurons.adex(N, t, ns_x, ts_x, 
                                  w_in=w_in, 
                                  bias_in=bias_in-A/2, 
                                  sigma=0, 
                                  A=A, f=30, **params)

In [ ]:
# Extract budgets
combine = True
ns_first, ts_first = locate_firsts(ns_y, ts_y, combine=combine)
voltages_m = filter_voltages(
    budget_y,
    ns_first,
    ts_first,
    budget_delay=-2e-3,
    budget_width=2e-3,
    combine=combine)

times = budget_y['times']


p = figure(plot_width=400, plot_height=200)

fulls = []
wins = []
labels_f = []
labels_w = []
for i, n in enumerate(set(ns_y)):
    v = voltages_m['V_m'][i, :]
    if not combine:
        times = voltages_m['times'][i, :]
    else:
        times = voltages_m['times']
    
    p.line(x=times, y=v, color="blue", alpha=0.5, line_width=3)
    
    v_full = budget_y['V_m'][n, :]
    times_full = budget_y['times']
    p.line(x=times_full, y=v_full, color="black", alpha=0.5, line_width=0.5)
    
    fulls.append(v_full)
    wins.append(v)
    
    labels_f.append(np.repeat(n, v_full.size))
    labels_w.append(np.repeat(n, v.size))
    
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
# p.x_range = Range1d(0.63, 0.7)
p.y_range = Range1d(-66e-3, -48e-3)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [ ]:
ts_first

## Save examples ....

to replot in R (ensuring consistency with other plots)

In [ ]:
np.savetxt("../analysis/vm_full_examples.csv", 
           np.vstack([times_full, np.vstack(fulls)]).T, 
           delimiter=",", 
           header=",".join(["t"] + [str(n) for n in range(N)]), 
           comments="")

np.savetxt("../analysis/vm_window_examples_d2_w2.csv", 
           np.vstack([times, np.vstack(wins)]).T, 
           delimiter=",", 
           header=",".join(["t"] + [str(n) for n in range(N)]), 
           comments="")

# Membrane noise

In [ ]:
from numpy.random import normal

# Create data
times = fsutil.create_times(0.1, 1e-4)
y = normal(0, .001, times.size)

# Plot
p = figure(plot_width=300, plot_height=30, toolbar_location=None)

p.line(x=times, y=y, color="blue", alpha=0.6)

p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
p.yaxis.axis_label = 'Membrane voltages'
p.xaxis.axis_label = 'Time (s)'
#     p.xaxis.axis_label_text_font_size = '10pt'
p.yaxis.axis_label_text_font_size = '10pt'

p.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks

p.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
p.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
p.yaxis.major_label_text_font_size = '0pt'  # turn off y-axis tick labels
#     p.xaxis.major_label_text_font_size = '10pt'  # turn off y-axis tick labels
p.axis.visible = False
show(p)

# Single neuron decomp

In [8]:
t = 0.4
stim_number = 40
stim_onset = 0.2
stim_offset = 0.350
stim_rate = 6
dt = 1e-5
seed_stim = 1
ns_x, ts_x = util.poisson_impulse(
        t,
        stim_onset,
        stim_offset - stim_onset,
        stim_rate,
        n=stim_number,
        dt=dt,
        seed=None)

print(">>> {} spikes".format(ts_x.size))
print(">>> {} population rate".format(ts_x.size / (stim_offset - stim_onset)))

>>> 33 spikes
>>> 220.00000000000006 population rate


In [9]:
params, w_in, bias_in, sigma = util.read_modes(mode)
bias_in = np.asarray(bias_in)

N = 20
A = 0.2e-9 
ns_y, ts_y, budget_y = neurons.adex(N, t, ns_x, ts_x, 
                                  w_in=w_in, 
                                  bias_in=bias_in-A/2, 
                                  sigma=0, 
                                  A=A, f=30, **params)

WARNING    "a" is an internal variable of group "neurongroup", but also exists in the run namespace with the value 2e-09. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "tau_w" is an internal variable of group "neurongroup", but also exists in the run namespace with the value 0.3. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "g_l" is an internal variable of group "neurongroup", but also exists in the run namespace with the value 1.2e-08. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "bias_in" is an internal variable of group "neurongroup", but also exists in the run namespace with the value -5e-11. The internal variable will be used. [brian2.groups.group.Group.resolve.resolution_conflict]
WARNING    "b" is an internal variable of group "neurongroup", but also exists in the run namespace with the value 6e-11. The inter

In [10]:
n = 1

In [11]:
times = budget_y['times']
v_c = budget_y['V_comp'][n, :]

p = figure(plot_width=400, plot_height=200)
p.line(x=times, y=-70e-3 - v_c, color="purple")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [12]:
times = budget_y['times']
v_o = budget_y['V_osc'][n, :]

p = figure(plot_width=400, plot_height=200)
p.line(x=times, y=-70e-3 - v_o, color="red")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [13]:
p = figure(plot_width=400, plot_height=200)
p.line(x=times, y=-70e-3 - v_c - v_o, color="blue")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [14]:
p = figure(plot_width=400, plot_height=200)
p.line(x=times, y=-70e-3 - v_o, color="red")
p.line(x=times, y=-70e-3 - v_c - v_o, color="purple")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [15]:
vs = np.vstack([times, -70e-3 - v_o, -70e-3 - v_c - v_o, -70e-3 - v_c - v_o]).T
header = "t,osc,comp,vm"

In [16]:
np.savetxt("../analysis/vm_comp_timecourse.csv", 
           vs,
           delimiter=",", 
           header=header,
           comments="")

In [ ]:
ts_y